### Weather table

This table is prebuilt from individual forecast.io queries.  Code for doing this is in the data collection notebook.

In [6]:
import pandas as pd

In [7]:
weather_file = "/Users/zcarwile/Documents/content/sales_engineering_demos/citibike/weatherTable/weather.csv"
weather_df = pd.read_csv(weather_file)

In [8]:
weather_df.head()

TS_year  TS_month  TS_day  TS_hour  TS_minute  cloudCover        summary  \
0   2016.0       9.0    29.0     10.0       45.0        1.00       Overcast   
1   2016.0       7.0    27.0     12.0       10.0        0.17          Clear   
2   2016.0       9.0    20.0      0.0        5.0        0.66  Mostly Cloudy   
3   2016.0       9.0     9.0      6.0       45.0        0.36  Partly Cloudy   
4   2016.0       7.0    21.0     12.0       20.0        0.04          Clear   

   visibility nearestStormBearing   ozone    ...    windSpeed  windBearing  \
0        9.59               334.0  291.75    ...         9.32         50.0   
1        9.67               270.0  300.19    ...         3.00          0.0   
2        9.30               115.0   269.0    ...         2.90        189.0   
3        9.39               325.0  266.65    ...         5.56        242.0   
4        9.39               260.0  320.91    ...         4.32        276.0   

   apparentTemperature          time  humidity  nearestStormDistance  \
0                61.46  1.475146e+09      0.82                   9.0   
1                78.06  1.469621e+09      0.64                  23.0   
2                69.50  1.474330e+09      0.90                  14.0   
3                79.62  1.473404e+09      0.73                  14.0   
4                74.63  1.469104e+09      0.72                  66.0   

   temperature dewPoint  precipProbability  pressure  
0        61.46    56.07                0.0   1025.20  
1        78.06    65.00                0.0   1013.78  
2        69.50    66.51                0.0   1017.51  
3        79.62    70.07                0.0   1009.81  
4        74.63    64.81                0.0   1021.58  

[5 rows x 22 columns]

In [9]:
weather_df.sort_values(by=["TS_year","TS_month","TS_day","TS_hour","TS_minute"])[['apparentTemperature','humidity']].head()

apparentTemperature  humidity
23900                91.41      0.73
17037                92.15      0.73
8890                 91.68      0.73
15072                91.93      0.73
2056                 92.93      0.71

### Bike Availability Data

We need to stitch together the 5-minute bike availability data into a longer history for each station.  We can use a few months for training and another month for testing our model.

In [10]:
import os
import datetime

dir = "./bikeDataCSV"
#dir = "./bikeDataCSV_Sept"

#station = "E 72 St & Park Ave"
station = "W 47 St & 10 Ave"
#station="Pershing Square North"

columns = ['lastCommunicationTime','latitude','longitude','availableBikes','availableDocks','statusValue']
addlColumns = ['TS_year','TS_month','TS_day','TS_hour','TS_minute','timestamp','weekday']
allColumns = columns + addlColumns

In [11]:
# This may take a little while

station_df = pd.DataFrame(columns=allColumns)
i = 0

for file in os.listdir(dir):
    
    if file.endswith(".csv") == False:
        continue

    df = pd.read_csv(os.path.join(dir,file))
    df_subset = df.loc[df['stationName'] == station][columns]
    
    TS = file.split("_")[1].split(".csv")[0]
    df_subset['TS_year'] = int(TS[0:4])
    df_subset['TS_month'] = int(TS[4:6])
    df_subset['TS_day'] = int(TS[6:8])
    df_subset['TS_hour'] = int(TS[8:10])
    df_subset['TS_minute'] = int(TS[10:12])
    TSDT = datetime.datetime(int(TS[0:4]),int(TS[4:6]),int(TS[6:8]),int(TS[8:10]),int(TS[10:12]),0)
    df_subset['timestamp'] = TSDT
    df_subset['weekday'] = TSDT.weekday()
    
    station_df = pd.concat([station_df, df_subset],ignore_index=True)
    
    #i = i + 1
    #if i > 10:
    #    break

#station_df.to_csv(station.replace(" ","_") + ".csv", index=False)

In [21]:
station_df.tail()

lastCommunicationTime   latitude  longitude  availableBikes  \
33078  2016-11-10 10:09:24 AM  40.762699 -73.993012             2.0   
33079  2016-11-10 10:15:13 AM  40.762699 -73.993012             0.0   
33080  2016-11-10 10:19:12 AM  40.762699 -73.993012             0.0   
33081  2016-11-10 10:23:10 AM  40.762699 -73.993012             0.0   
33082  2016-11-10 10:27:23 AM  40.762699 -73.993012             1.0   

       availableDocks statusValue  TS_year  TS_month  TS_day  TS_hour  \
33078            23.0  In Service   2016.0      11.0    10.0     15.0   
33079            25.0  In Service   2016.0      11.0    10.0     15.0   
33080            25.0  In Service   2016.0      11.0    10.0     15.0   
33081            25.0  In Service   2016.0      11.0    10.0     15.0   
33082            24.0  In Service   2016.0      11.0    10.0     15.0   

       TS_minute           timestamp  weekday  
33078       10.0 2016-11-10 15:10:00      3.0  
33079       15.0 2016-11-10 15:15:00      3.0  
33080       20.0 2016-11-10 15:20:00      3.0  
33081       25.0 2016-11-10 15:25:00      3.0  
33082       30.0 2016-11-10 15:30:00      3.0

### Feature matrix

In [22]:
weather_df.tail()

TS_year  TS_month  TS_day  TS_hour  TS_minute  temperature  humidity  \
34165   2016.0       8.0    16.0      9.0        5.0        76.70      0.82   
34166   2016.0      10.0    23.0     10.0       50.0        44.10      0.68   
34167   2016.0       7.0    23.0     16.0       10.0        90.50      0.38   
34168   2016.0       7.0    25.0      3.0       55.0        79.74      0.68   
34169   2016.0       7.0    16.0     21.0       30.0        79.96      0.69   

       precipProbability  cloudCover                 icon  windSpeed   ozone  
34165               0.00        0.52  partly-cloudy-night       2.42  283.76  
34166               0.00        0.23          clear-night      11.90  295.64  
34167               0.00        0.04            clear-day       7.05  295.22  
34168               0.00        0.14          clear-night       5.09  289.09  
34169               0.18        0.44    partly-cloudy-day       7.37  305.59

In [23]:
weatherColumns = ['TS_year','TS_month','TS_day','TS_hour', \
                'TS_minute','temperature','humidity','precipProbability','cloudCover','icon','windSpeed','ozone']
weather_df = weather_df[weatherColumns]
weather_df.tail()

TS_year  TS_month  TS_day  TS_hour  TS_minute  temperature  humidity  \
34165   2016.0       8.0    16.0      9.0        5.0        76.70      0.82   
34166   2016.0      10.0    23.0     10.0       50.0        44.10      0.68   
34167   2016.0       7.0    23.0     16.0       10.0        90.50      0.38   
34168   2016.0       7.0    25.0      3.0       55.0        79.74      0.68   
34169   2016.0       7.0    16.0     21.0       30.0        79.96      0.69   

       precipProbability  cloudCover                 icon  windSpeed   ozone  
34165               0.00        0.52  partly-cloudy-night       2.42  283.76  
34166               0.00        0.23          clear-night      11.90  295.64  
34167               0.00        0.04            clear-day       7.05  295.22  
34168               0.00        0.14          clear-night       5.09  289.09  
34169               0.18        0.44    partly-cloudy-day       7.37  305.59

In [24]:
big_df = station_df.merge(weather_df, on=['TS_year','TS_month','TS_day','TS_hour','TS_minute'], how='left')
big_df.head()

lastCommunicationTime   latitude  longitude  availableBikes  \
0  2016-07-14 01:54:17 PM  40.762699 -73.993012             0.0   
1  2016-07-14 01:56:45 PM  40.762699 -73.993012             1.0   
2  2016-07-14 02:04:41 PM  40.762699 -73.993012             1.0   
3  2016-07-14 02:06:36 PM  40.762699 -73.993012             2.0   
4  2016-07-14 02:12:28 PM  40.762699 -73.993012             3.0   

   availableDocks statusValue  TS_year  TS_month  TS_day  TS_hour  TS_minute  \
0            24.0  In Service   2016.0       7.0    14.0     17.0       55.0   
1            23.0  In Service   2016.0       7.0    14.0     18.0        0.0   
2            23.0  In Service   2016.0       7.0    14.0     18.0        5.0   
3            22.0  In Service   2016.0       7.0    14.0     18.0       10.0   
4            21.0  In Service   2016.0       7.0    14.0     18.0       15.0   

            timestamp  weekday  temperature  humidity  precipProbability  \
0 2016-07-14 17:55:00      3.0        83.93      0.73                0.0   
1 2016-07-14 18:00:00      3.0        84.32      0.73                0.0   
2 2016-07-14 18:05:00      3.0        84.12      0.73                0.0   
3 2016-07-14 18:10:00      3.0        84.22      0.73                0.0   
4 2016-07-14 18:15:00      3.0        84.87      0.71                0.0   

   cloudCover               icon  windSpeed   ozone  
0        0.31  partly-cloudy-day       5.97  320.92  
1        0.33  partly-cloudy-day       5.76  320.92  
2        0.35  partly-cloudy-day       8.90  320.99  
3        0.37  partly-cloudy-day       8.97  321.07  
4        0.26  partly-cloudy-day       8.57  321.14

In [25]:
# Should probably apply this transform to the whole feature matrix
datetime.datetime.today().weekday()

2

In [26]:
big_df.to_csv("features_" + station.replace(" ","_") + ".csv", index=False)
#big_df.to_csv("features_" + station.replace(" ","_") + "_Sept.csv", index=False)

### Availability trend (one station)

In [31]:
from bokeh.plotting import figure, output_notebook, show
output_notebook()

Loading BokehJS ...

In [ ]:
TOOLS = ['box_zoom','wheel_zoom','pan','resize','hover','reset']
p = figure(x_axis_type="datetime", tools=TOOLS)
p.line(big_df['timestamp'], big_df['temperature'], color='blue', legend="Temperature")
p.line(big_df['timestamp'], big_df['availableBikes'], color='red', legend="Bikes")
#p.line(big_df['timestamp'], 100*big_df['humidity'], color='red')
#p.line(big_df['timestamp'], 100*big_df['precipProbability'], color='green')

show(p)

### Station List

In [32]:
# crude code to get station list

station_list = pd.Series()

for file in os.listdir(dir):
    
    if file.endswith(".csv") == False:
        continue
        
    df = pd.read_csv(os.path.join(dir,file))
    station_list = df.loc[df['statusValue'] == "In Service"]['stationName']
    break

for ind, val in station_list.iteritems():
    print(val)

W 52 St & 11 Ave
Franklin St & W Broadway
St James Pl & Pearl St
Atlantic Ave & Fort Greene Pl
W 17 St & 8 Ave
Park Ave & St Edwards St
Lexington Ave & Classon Ave
Barrow St & Hudson St
MacDougal St & Prince St
E 56 St & Madison Ave
Clinton St & Joralemon St
Nassau St & Navy St
Hudson St & Reade St
Greenwich St & Warren St
E 2 St & Avenue C
Cleveland Pl & Spring St
Warren St & Church St
E 40 St & 5 Ave
Henry St & Atlantic Ave
LaGuardia Pl & W 3 St
E 47 St & 2 Ave
E 39 St & 3 Ave
W 18 St & 6 Ave
Broadway & W 49 St
E 25 St & 1 Ave
Liberty St & Broadway
W 16 St & The High Line
Columbia Heights & Cranberry St
Old Fulton St
Spruce St & Nassau St
W 14 St & The High Line
E 48 St & 3 Ave
Great Jones St
Cadman Plaza E & Tillary St
St Marks Pl & 2 Ave
E 11 St & 2 Ave
Bank St & Washington St
Willoughby St & Fleet St
DeKalb Ave & S Portland Ave
Carlton Ave & Flushing Ave
Fulton St & Rockwell Pl
Willoughby Ave & Hall St
Myrtle Ave & St Edwards St
Perry St & Bleecker St
Laight St & Hudson St
Harriso

In [24]:
station_df['percentFull'] = station_df['availableBikes'] / (station_df['availableBikes'] + station_df['availableDocks'])
station_df.tail()

lastCommunicationTime   latitude  longitude  availableBikes  \
13860  2016-08-31 07:34:37 PM  40.762699 -73.993012             9.0   
13861  2016-08-31 07:39:21 PM  40.762699 -73.993012            10.0   
13862  2016-08-31 07:43:32 PM  40.762699 -73.993012            13.0   
13863  2016-08-31 07:45:27 PM  40.762699 -73.993012            13.0   
13864  2016-08-31 07:53:17 PM  40.762699 -73.993012            13.0   

       availableDocks statusValue  TS_year  TS_month  TS_day  TS_hour  \
13860            14.0  In Service   2016.0       8.0    31.0     23.0   
13861            13.0  In Service   2016.0       8.0    31.0     23.0   
13862            10.0  In Service   2016.0       8.0    31.0     23.0   
13863            10.0  In Service   2016.0       8.0    31.0     23.0   
13864            10.0  In Service   2016.0       8.0    31.0     23.0   

       TS_minute           timestamp  weekday  percentFull  
13860       35.0 2016-08-31 23:35:00      2.0     0.391304  
13861       40.0 2016-08-31 23:40:00      2.0     0.434783  
13862       45.0 2016-08-31 23:45:00      2.0     0.565217  
13863       50.0 2016-08-31 23:50:00      2.0     0.565217  
13864       55.0 2016-08-31 23:55:00      2.0     0.565217

In [25]:
big_df.tail()

lastCommunicationTime   latitude  longitude  availableBikes  \
13860  2016-08-31 07:34:37 PM  40.762699 -73.993012             9.0   
13861  2016-08-31 07:39:21 PM  40.762699 -73.993012            10.0   
13862  2016-08-31 07:43:32 PM  40.762699 -73.993012            13.0   
13863  2016-08-31 07:45:27 PM  40.762699 -73.993012            13.0   
13864  2016-08-31 07:53:17 PM  40.762699 -73.993012            13.0   

       availableDocks statusValue  TS_year  TS_month  TS_day  TS_hour  \
13860            14.0  In Service   2016.0       8.0    31.0     23.0   
13861            13.0  In Service   2016.0       8.0    31.0     23.0   
13862            10.0  In Service   2016.0       8.0    31.0     23.0   
13863            10.0  In Service   2016.0       8.0    31.0     23.0   
13864            10.0  In Service   2016.0       8.0    31.0     23.0   

       TS_minute           timestamp  weekday  temperature  humidity  \
13860       35.0 2016-08-31 23:35:00      2.0        79.91      0.72   
13861       40.0 2016-08-31 23:40:00      2.0        79.82      0.72   
13862       45.0 2016-08-31 23:45:00      2.0        79.74      0.72   
13863       50.0 2016-08-31 23:50:00      2.0        79.64      0.72   
13864       55.0 2016-08-31 23:55:00      2.0        79.16      0.71   

       precipProbability  cloudCover                 icon  windSpeed   ozone  
13860                0.0        0.26  partly-cloudy-night       3.76  291.18  
13861                0.0        0.28  partly-cloudy-night       3.87  291.13  
13862                0.0        0.29  partly-cloudy-night       3.98  291.07  
13863                0.0        0.30  partly-cloudy-night       4.09  291.02  
13864                0.0        0.27  partly-cloudy-night       4.21  290.97